# Azure Data Engineering Project Overview

This document provides a comprehensive overview of the end-to-end data engineering workflow implemented in Azure. It details the setup and processes for managing data from ingestion through to transformation and export, including the configuration for secure data access.

## Workflow Summary

1. **Storage Configuration:** Azure Data Lake Storage (ADLS) Gen2 is mounted with OAuth authentication to ensure secure and efficient access to the data lake.
2. **Data Ingestion:** Data is ingested from CSV files into Spark DataFrames, and temporary SQL views are created for data querying and manipulation.
3. **Data Transformation:** SQL queries are employed to clean, transform, and enrich the data, preparing it for subsequent analysis and reporting.
4. **Data Export:** The transformed datasets are written back to ADLS Gen2 as CSV files, ensuring they are ready for further use or analysis.



In [0]:
from pyspark.sql import functions as F

## Mount Azure Data Lake Storage

Azure Data Lake Storage (ADLS) Gen2 is mounted to the Databricks file system using OAuth authentication. Configuration details include client ID, client secret, and token endpoint to securely access the data in the specified container.



In [0]:
configs = {"fs.azure.account.auth.type": "OAuth",
"fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
"fs.azure.account.oauth2.client.id": "x",
"fs.azure.account.oauth2.client.secret": 'x',
"fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/x/oauth2/token"}


dbutils.fs.mount(
 source = "abfss://paris-olympic-data@parisolympicdata123.dfs.core.windows.net", # contrainer@storageacc
 mount_point = "/mnt/parisolymics",
 extra_configs = configs)

In [0]:

%fs
ls "/mnt/parisolymics"

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$5(SequenceExecutionState.scala:136)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:136)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:727)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:445)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ChauffeurState.cancelExecutio

## Data Loading and Inspection

1. **Load Data:**
   Data is loaded from CSV files into DataFrames for athletes, coaches, medals, and teams with headers and automatic schema inference.

2. **Inspect Schema:**
   The schema of the teams DataFrame is displayed to review column names and data types.


In [0]:
athletes = spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/parisolymics/raw-data/athletes.csv")
coaches = spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/parisolymics/raw-data/coaches.csv")
medals = spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/parisolymics/raw-data/medals.csv")
teams = spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/parisolymics/raw-data/teams.csv")

teams.printSchema()

root
 |-- code: string (nullable = true)
 |-- current: boolean (nullable = true)
 |-- team: string (nullable = true)
 |-- team_gender: string (nullable = true)
 |-- country_code: string (nullable = true)
 |-- country: string (nullable = true)
 |-- country_long: string (nullable = true)
 |-- discipline: string (nullable = true)
 |-- disciplines_code: string (nullable = true)
 |-- events: string (nullable = true)
 |-- athletes: string (nullable = true)
 |-- coaches: string (nullable = true)
 |-- athletes_codes: string (nullable = true)
 |-- num_athletes: string (nullable = true)
 |-- coaches_codes: string (nullable = true)
 |-- num_coaches: string (nullable = true)



## Create Temporary Views

1. **Create Views:**
   Temporary views are created for the athletes, coaches, medals, and teams DataFrames, allowing SQL queries to be run against them.


## Data Processing and Transformation

1. **Create Temporary Views:**
   - Temporary views are created for the athletes, coaches, medals, and teams DataFrames to facilitate SQL queries.

2. **Query and Transform Data:**
   - **Athletes Data:** A SQL query selects and transforms fields, calculates age, and formats the discipline.
   - **Medals Data:** A SQL query cleans up the `medal_type` field, adjusts gender, and formats the output.
   - **Teams Data:** A SQL query cleans and splits arrays to expand athlete and athlete code information.

3. **Display Data:**
   - The transformed `athletes`, `medals`, `teams`, and `coaches` data is displayed to review the results of the transformations.


In [0]:
%sql
select 
      code,
      name,
      name_short,
      name_tv,
      country,
      country_code,
      nationality,
      gender,
      birth_date,
      FLOOR(DATEDIFF(CURRENT_DATE, birth_date) / 365.25) AS age,
      SUBSTRING(disciplines, 3, LENGTH(disciplines) - 4) AS discipline
from athletes_view

code name name_short name_tv country country_code nationality gender birth_date age discipline 1532872 ALEKSANYAN Artur ALEKSANYAN A Artur ALEKSANYAN Armenia ARM Armenia Male 1991-10-21 32 Wrestling 1532873 AMOYAN Malkhas AMOYAN M Malkhas AMOYAN Armenia ARM Armenia Male 1999-01-22 25 Wrestling 1532874 GALSTYAN Slavik GALSTYAN S Slavik GALSTYAN Armenia ARM Armenia Male 1996-12-21 27 Wrestling 1532944 HARUTYUNYAN Arsen HARUTYUNYAN A Arsen HARUTYUNYAN Armenia ARM Armenia Male 1999-11-22 24 Wrestling 1532945 TEVANYAN Vazgen TEVANYAN V Vazgen TEVANYAN Armenia ARM Armenia Male 1999-10-27 24 Wrestling 1532951 ARENAS Lorena ARENAS L Lorena ARENAS Colombia COL Colombia Female 1993-09-17 30 Athletics 1533112 McKENZIE Ashley McKENZIE A Ashley McKENZIE Jamaica JAM Jamaica Male 1989-07-17 35 Judo 1533136 BASS BITTAYE Gina Mariam BASS BITTAYE GM Gina Mariam BASS BITTAYE Gambia GAM Gambia Female 1995-05-03 29 Athletics 1533176 CAMARA Ebrahima CAMARA E Ebrahima CAMARA Gambia GAM Gambia Male 1996-09-18 27 Athletics 1533188 RUEDA SANTOS Lizeth RUEDA SANTOS L Lizeth RUEDA SANTOS Mexico MEX Mexico Female 1994-03-07 30 Triathlon 1533189 TAPIA VIDAL Rosa Maria TAPIA VIDAL RM Rosa Maria TAPIA VIDAL Mexico MEX Mexico Female 1997-08-27 27 Triathlon 1533190 GRAJALES Crisanto GRAJALES C Crisanto GRAJALES Mexico MEX Mexico Male 1987-05-06 37 Triathlon 1533208 MAAROUFOU Hachim MAAROUFOU H Hachim MAAROUFOU Comoros COM Comoros Male 1997-02-13 27 Athletics 1533209 SAADI Maesha SAADI M Maesha SAADI Comoros COM Comoros Female 2007-01-16 17 Swimming 1533230 DIOSDADO Nuria DIOSDADO N Nuria DIOSDADO Mexico MEX Mexico Female 1990-08-22 34 Artistic Swimming 1533231 JIMENEZ Joana JIMENEZ J Joana JIMENEZ Mexico MEX Mexico Female 1993-08-19 31 Artistic Swimming 1533232 SOBRINO Jessica SOBRINO J Jessica SOBRINO Mexico MEX Mexico Female 1994-05-26 30 Artistic Swimming 1533234 ALFEREZ Regina ALFEREZ R Regina ALFEREZ Mexico MEX Mexico Female 1997-12-01 26 Artistic Swimming 1533235 ARELLANO Fernanda ARELLANO F Fernanda ARELLANO Mexico MEX Mexico Female 2002-02-28 22 Artistic Swimming 1533237 TOSCANO Pamela TOSCANO P Pamela TOSCANO Mexico MEX Mexico Female 2000-01-13 24 Artistic Swimming 1533239 GONZALEZ Itzamary GONZALEZ I Itzamary GONZALEZ Mexico MEX Mexico Female 2003-11-14 20 Artistic Swimming 1533240 RODRIGUEZ Samanta RODRIGUEZ S Samanta RODRIGUEZ Mexico MEX Mexico Female 1994-12-05 29 Artistic Swimming 1533243 INZUNZA Glenda INZUNZA G Glenda INZUNZA Mexico MEX Mexico Female 2000-03-12 24 Artistic Swimming 1533245 SEHEN Sajjad SEHEN S Sajjad SEHEN Iraq IRQ Iraq Male 1996-03-08 28 Judo 1533359 RUBAIAWI Ali Ammar Yusur RUBAIAWI AAY Ali Ammar Yusur RUBAIAWI Iraq IRQ Iraq Male 2004-08-02 20 Weightlifting 1533364 ISMAIL Mohamed ISMAIL M Mohamed ISMAIL Djibouti DJI Djibouti Male 1997-01-01 27 Athletics 1533371 HASSAN Ibrahim HASSAN I Ibrahim HASSAN Djibouti DJI Djibouti Male 1997-01-01 27 Athletics 1533372 WAISS Abdi WAISS A Abdi WAISS Djibouti DJI Djibouti Male 1996-07-03 28 Athletics 1533374 HASSAN NOUR Samiyah HASSAN NOUR S Samiyah HASSAN NOUR Djibouti DJI Djibouti Female 1999-12-05 24 Athletics 1533378 HOUSSEIN BARKAT Houmed HOUSSEIN BARKAT H Houmed HOUSSEIN BARKAT Djibouti DJI Djibouti Male 2004-04-04 20 Swimming 1535180 BARAT Andy BARAT A Andy BARAT Comoros COM Comoros Male 1997-11-29 26 Canoe Slalom 1535186 MARTINEZ RAMIREZ Miguel Angel MARTINEZ RAMIREZ M Miguel Angel MARTINEZ RAMIREZ Mexico MEX Mexico Male 2001-03-17 23 Boxing 1535187 VERDE ALVAREZ Marco Alonso VERDE ALVAREZ MA Marco Alonso VERDE ALVAREZ Mexico MEX Mexico Male 2002-02-11 22 Boxing 1535191 GONZALEZ Alegna GONZALEZ A Alegna GONZALEZ Mexico MEX Mexico Female 1999-01-02 25 Athletics 1535195 LOPEZ Jesus Tonatiu LOPEZ JT Jesus Tonatiu LOPEZ Mexico MEX Mexico Male 1997-08-02 27 Athletics 1535199 PORTILLO Erick PORTILLO E Erick PORTILLO Mexico MEX Mexico Male 2000-10-05 23 Athletics 1535201 MUNOZ Uziel MUNOZ U Uziel MUNOZ Mexico MEX Mexico Male 1995-09-08 28 Athletics 1535202 del REAL Diego del REAL D Diego 

In [0]:
athletes = _sqldf
athletes.show()

+-------+--------------------+---------------+--------------------+--------+------------+-----------+------+----------+---+-----------------+
|   code|                name|     name_short|             name_tv| country|country_code|nationality|gender|birth_date|age|       discipline|
+-------+--------------------+---------------+--------------------+--------+------------+-----------+------+----------+---+-----------------+
|1532872|    ALEKSANYAN Artur|   ALEKSANYAN A|    Artur ALEKSANYAN| Armenia|         ARM|    Armenia|  Male|1991-10-21| 32|        Wrestling|
|1532873|      AMOYAN Malkhas|       AMOYAN M|      Malkhas AMOYAN| Armenia|         ARM|    Armenia|  Male|1999-01-22| 25|        Wrestling|
|1532874|     GALSTYAN Slavik|     GALSTYAN S|     Slavik GALSTYAN| Armenia|         ARM|    Armenia|  Male|1996-12-21| 27|        Wrestling|
|1532944|   HARUTYUNYAN Arsen|  HARUTYUNYAN A|   Arsen HARUTYUNYAN| Armenia|         ARM|    Armenia|  Male|1999-11-22| 24|        Wrestling|
|15329

In [0]:
%sql
select REPLACE(TRIM(medal_type), ' Medal', '') AS medal_type,
        medal_code, 
        medal_date,
        name,
        case when gender = 'W' then 'Female' else 'Male' end as gender,
        discipline,
        event,
        event_type,
        code,
        country_code,
        country,
        country_long
from medals_view

medal_type medal_code medal_date name gender discipline event event_type code country_code country country_long Gold 1.0 2024-07-27 Remco EVENEPOEL Male Cycling Road Men's Individual Time Trial ATH 1903136 BEL Belgium Belgium Silver 2.0 2024-07-27 Filippo GANNA Male Cycling Road Men's Individual Time Trial ATH 1923520 ITA Italy Italy Bronze 3.0 2024-07-27 Wout van AERT Male Cycling Road Men's Individual Time Trial ATH 1903147 BEL Belgium Belgium Gold 1.0 2024-07-27 Grace BROWN Female Cycling Road Women's Individual Time Trial ATH 1940173 AUS Australia Australia Silver 2.0 2024-07-27 Anna HENDERSON Female Cycling Road Women's Individual Time Trial ATH 1912525 GBR Great Britain Great Britain Bronze 3.0 2024-07-27 Chloe DYGERT Female Cycling Road Women's Individual Time Trial ATH 1955079 USA United States United States of America Gold 1.0 2024-07-27 China Female Diving Women's Synchronised 3m Springboard TEAM DIVW3MTEAM2-CHN01 CHN China People's Republic of China Silver 2.0 2024-07-27 United States Female Diving Women's Synchronised 3m Springboard TEAM DIVW3MTEAM2-USA01 USA United States United States of America Bronze 3.0 2024-07-27 Great Britain Female Diving Women's Synchronised 3m Springboard TEAM DIVW3MTEAM2-GBR01 GBR Great Britain Great Britain Gold 1.0 2024-07-27 OH Sanguk Male Fencing Men's Sabre Individual HATH 1927149 KOR Korea Republic of Korea Silver 2.0 2024-07-27 Fares FERJANI Male Fencing Men's Sabre Individual HATH 1937783 TUN Tunisia Tunisia Bronze 3.0 2024-07-27 Luigi SAMELE Male Fencing Men's Sabre Individual HATH 1924595 ITA Italy Italy Gold 1.0 2024-07-27 KONG Man Wai Vivian Female Fencing Women's Épée Individual HATH 1963262 HKG Hong Kong, China Hong Kong, China Silver 2.0 2024-07-27 Auriane MALLO-BRETON Female Fencing Women's Épée Individual HATH 1916183 FRA France France Bronze 3.0 2024-07-27 Eszter MUHARI Female Fencing Women's Épée Individual HATH 1946375 HUN Hungary Hungary Gold 1.0 2024-07-27 Yeldos SMETOV Male Judo Men -60 kg HATH 1935408 KAZ Kazakhstan Kazakhstan Silver 2.0 2024-07-27 Luka MKHEIDZE Male Judo Men -60 kg HATH 1891304 FRA France France Bronze 3.0 2024-07-27 NAGAYAMA Ryuju Male Judo Men -60 kg HATH 1896752 JPN Japan Japan Bronze 3.0 2024-07-27 Francisco GARRIGOS Male Judo Men -60 kg HATH 1563544 ESP Spain Spain Gold 1.0 2024-07-27 TSUNODA Natsumi Female Judo Women -48 kg HATH 1896735 JPN Japan Japan Silver 2.0 2024-07-27 Baasankhuu BAVUUDORJ Female Judo Women -48 kg HATH 1914467 MGL Mongolia Mongolia Bronze 3.0 2024-07-27 Shirine BOUKLI Female Judo Women -48 kg HATH 1891280 FRA France France Bronze 3.0 2024-07-27 Tara BABULFATH Female Judo Women -48 kg HATH 1571911 SWE Sweden Sweden Gold 1.0 2024-07-27 France Male Rugby Sevens Men HTEAM RU7MTEAM7---FRA01 FRA France France Silver 2.0 2024-07-27 Fiji Male Rugby Sevens Men HTEAM RU7MTEAM7---FIJ01 FIJ Fiji Fiji Bronze 3.0 2024-07-27 South Africa Male Rugby Sevens Men HTEAM RU7MTEAM7---RSA01 RSA South Africa South Africa Gold 1.0 2024-07-27 China 1 Male Shooting 10m Air Rifle Mixed Team HTEAM SHOXARMT----CHN01 CHN China People's Republic of China Silver 2.0 2024-07-27 Korea 1 Male Shooting 10m Air Rifle Mixed Team HTEAM SHOXARMT----KOR01 KOR Korea Republic of Korea Bronze 3.0 2024-07-27 Kazakhstan 1 Male Shooting 10m Air Rifle Mixed Team HTEAM SHOXARMT----KAZ01 KAZ Kazakhstan Kazakhstan Gold 1.0 2024-07-27 United States Male Swimming Men's 4 x 100m Freestyle Relay TEAM SWMM4X100MFRUSA01 USA United States United States of America Silver 2.0 2024-07-27 Australia Male Swimming Men's 4 x 100m Freestyle Relay TEAM SWMM4X100MFRAUS01 AUS Australia Australia Bronze 3.0 2024-07-27 Italy Male Swimming Men's 4 x 100m Freestyle Relay TEAM SWMM4X100MFRITA01 ITA Italy Italy Gold 1.0 2024-07-27 Lukas MAERTENS Male Swimming Men's 400m Freestyle ATH 1907192 GER Germany Germany Silver 2.0 2024-07-27 Elijah WINNINGTON Male Swimming Men's 400m Freestyle ATH 1946172 AUS Australia Australia Bronze 3.0 2024-07-27 KIM Woomin Male Swimming Men's 400m Freestyle ATH 46

In [0]:
medals = _sqldf
medals.show()

+----------+----------+----------+--------------------+------+------------+--------------------+----------+-----------------+------------+----------------+--------------------+
|medal_type|medal_code|medal_date|                name|gender|  discipline|               event|event_type|             code|country_code|         country|        country_long|
+----------+----------+----------+--------------------+------+------------+--------------------+----------+-----------------+------------+----------------+--------------------+
|      Gold|       1.0|2024-07-27|     Remco EVENEPOEL|  Male|Cycling Road|Men's Individual ...|       ATH|          1903136|         BEL|         Belgium|             Belgium|
|    Silver|       2.0|2024-07-27|       Filippo GANNA|  Male|Cycling Road|Men's Individual ...|       ATH|          1923520|         ITA|           Italy|               Italy|
|    Bronze|       3.0|2024-07-27|       Wout van AERT|  Male|Cycling Road|Men's Individual ...|       ATH|        

In [0]:
%sql
with cleaned_data as (
    select
        code,
        current,
        team,
        team_gender,
        country_code,
        country,
        country_long,
        discipline,
        disciplines_code,
        events,
        split(translate(trim(athletes), '[]\'', ''), ', ') as athlete_array,
        split(translate(trim(athletes_codes), '[]\'', ''), ', ') as athlete_code_array
    from teams_view
)
    select
        code,
        current,
        team,
        case when team_gender = 'M' then 'Male' when team_gender = 'W' then 'Female' else 'X' end as team_gender,
        country_code,
        country,
        country_long,
        discipline,
        disciplines_code,
        events,
        athlete as athlete_name,
        athlete_code
    from cleaned_data
    lateral view posexplode(athlete_array) as pos, athlete
    lateral view posexplode(athlete_code_array) as pos_code, athlete_code
    where pos = pos_code

code current team team_gender country_code country country_long discipline disciplines_code events athlete_name athlete_code ARCMTEAM3---CHN01 true People's Republic of China Male CHN China People's Republic of China Archery ARC Men's Team KAO Wenchao 1913366 ARCMTEAM3---CHN01 true People's Republic of China Male CHN China People's Republic of China Archery ARC Men's Team LI Zhongyuan 1913367 ARCMTEAM3---CHN01 true People's Republic of China Male CHN China People's Republic of China Archery ARC Men's Team WANG Yan 1913369 ARCMTEAM3---COL01 true Colombia Male COL Colombia Colombia Archery ARC Men's Team ARCILA Santiago 1935642 ARCMTEAM3---COL01 true Colombia Male COL Colombia Colombia Archery ARC Men's Team ENRIQUEZ Jorge 1543412 ARCMTEAM3---COL01 true Colombia Male COL Colombia Colombia Archery ARC Men's Team HERNANDEZ VERA Andres 1935644 ARCMTEAM3---FRA01 true France Male FRA France France Archery ARC Men's Team ADDIS Baptiste 1541270 ARCMTEAM3---FRA01 true France Male FRA France France Archery ARC Men's Team CHIRAULT Thomas 1541272 ARCMTEAM3---FRA01 true France Male FRA France France Archery ARC Men's Team VALLADONT Jean-Charles 1541275 ARCMTEAM3---GBR01 true Great Britain Male GBR Great Britain Great Britain Archery ARC Men's Team HALL Conor 1560988 ARCMTEAM3---GBR01 true Great Britain Male GBR Great Britain Great Britain Archery ARC Men's Team HALL Tom 1560989 ARCMTEAM3---GBR01 true Great Britain Male GBR Great Britain Great Britain Archery ARC Men's Team WISE Alex 1561003 ARCMTEAM3---IND01 true India Male IND India India Archery ARC Men's Team BOMMADEVARA Dhiraj 1546108 ARCMTEAM3---IND01 true India Male IND India India Archery ARC Men's Team JADHAV Pravin Ramesh 1546112 ARCMTEAM3---IND01 true India Male IND India India Archery ARC Men's Team RAI Tarundeep 1546110 ARCMTEAM3---ITA01 true Italy Male ITA Italy Italy Archery ARC Men's Team MUSOLESI Federico 1915456 ARCMTEAM3---ITA01 true Italy Male ITA Italy Italy Archery ARC Men's Team NESPOLI Mauro 1915454 ARCMTEAM3---ITA01 true Italy Male ITA Italy Italy Archery ARC Men's Team PAOLI Alessandro 1915455 ARCMTEAM3---JPN01 true Japan Male JPN Japan Japan Archery ARC Men's Team FURUKAWA Takaharu 1890994 ARCMTEAM3---JPN01 true Japan Male JPN Japan Japan Archery ARC Men's Team NAKANISHI Junya 1890985 ARCMTEAM3---JPN01 true Japan Male JPN Japan Japan Archery ARC Men's Team SAITO Fumiya 1890977 ARCMTEAM3---KAZ01 true Kazakhstan Male KAZ Kazakhstan Kazakhstan Archery ARC Men's Team ABDULLIN Ilfat 1931570 ARCMTEAM3---KAZ01 true Kazakhstan Male KAZ Kazakhstan Kazakhstan Archery ARC Men's Team YEREMENKO Alexandr 1560342 ARCMTEAM3---KAZ01 true Kazakhstan Male KAZ Kazakhstan Kazakhstan Archery ARC Men's Team ZHANGBYRBAY Dauletkeldi 1931572 ARCMTEAM3---KOR01 true Republic of Korea Male KOR Korea Republic of Korea Archery ARC Men's Team KIM Je Deok 1902130 ARCMTEAM3---KOR01 true Republic of Korea Male KOR Korea Republic of Korea Archery ARC Men's Team KIM Woojin 1902135 ARCMTEAM3---KOR01 true Republic of Korea Male KOR Korea Republic of Korea Archery ARC Men's Team LEE Wooseok 1902144 ARCMTEAM3---MEX01 true Mexico Male MEX Mexico Mexico Archery ARC Men's Team GRANDE Matias 1535430 ARCMTEAM3---MEX01 true Mexico Male MEX Mexico Mexico Archery ARC Men's Team MARTINEZ WING Bruno 1536467 ARCMTEAM3---MEX01 true Mexico Male MEX Mexico Mexico Archery ARC Men's Team ROJAS Carlos 1536460 ARCMTEAM3---TPE01 true Chinese Taipei Male TPE Chinese Taipei Chinese Taipei Archery ARC Men's Team LIN Zih-Siang 1564631 ARCMTEAM3---TPE01 true Chinese Taipei Male TPE Chinese Taipei Chinese Taipei Archery ARC Men's Team TANG Chih-Chun 1564628 ARCMTEAM3---TPE01 true Chinese Taipei Male TPE Chinese Taipei Chinese Taipei Archery ARC Men's Team TAI Yu-Hsuan 1564630 ARCMTEAM3---TUR01 true Türkiye Male TUR Türkiye Türkiye Archery ARC Men's Team GAZOZ Mete 1565000 ARCMTEAM3---TUR01 true Türkiye Male TUR Türkiye Türkiye Archery ARC Men's Team TUMER Berkim 1565002 ARCMTEAM3---TUR01 true Türkiye Male TUR Türkiye Türkiye Arch

In [0]:
teams = _sqldf
teams.show()

+-----------------+-------+--------------------+-----------+------------+-------------+--------------------+----------+----------------+----------+--------------------+------------+
|             code|current|                team|team_gender|country_code|      country|        country_long|discipline|disciplines_code|    events|        athlete_name|athlete_code|
+-----------------+-------+--------------------+-----------+------------+-------------+--------------------+----------+----------------+----------+--------------------+------------+
|ARCMTEAM3---CHN01|   true|People's Republic...|       Male|         CHN|        China|People's Republic...|   Archery|             ARC|Men's Team|         KAO Wenchao|     1913366|
|ARCMTEAM3---CHN01|   true|People's Republic...|       Male|         CHN|        China|People's Republic...|   Archery|             ARC|Men's Team|        LI Zhongyuan|     1913367|
|ARCMTEAM3---CHN01|   true|People's Republic...|       Male|         CHN|        China|Peo

In [0]:
%sql
select *
from coaches_view

code current name gender function category country_code country country_long disciplines events birth_date 1533246 true PEDRERO Ofelia Female Coach C MEX Mexico Mexico Artistic Swimming Team 1988-03-28 1535775 true RADHI SHENAISHIL Male Head Coach C IRQ Iraq Iraq Football Men 1965-07-01 1536055 true AFLAKIKHAMSEH Majid Male Coach C IRI IR Iran Islamic Republic of Iran Taekwondo null 1973-08-26 1536059 true YOUSEFY Mehrdad Male Coach C IRI IR Iran Islamic Republic of Iran Taekwondo null 1972-06-12 1536060 true MADDAH Minoo Female Coach C IRI IR Iran Islamic Republic of Iran Taekwondo null 1976-05-17 1536328 true LOFTUS Adriana Female Coach C MEX Mexico Mexico Artistic Swimming Team 1958-06-28 1538313 true FERRARA Fernando Male Head Coach C ARG Argentina Argentina Hockey null 1968-07-24 1538315 true GULLA Alejandra Female Assistant Coach C ARG Argentina Argentina Hockey Women 1977-07-04 1538317 true CAPURRO Santiago Male Assistant Coach C ARG Argentina Argentina Hockey null 1975-04-08 1538745 true RONCONI Mariano Male Head Coach C ARG Argentina Argentina Hockey null null 1538748 true PAULON Ezequiel Male Assistant Coach C ARG Argentina Argentina Hockey null null 1538751 true VILA Matias Male Assistant Coach C ARG Argentina Argentina Hockey null null 1539598 true KHEIRKHAH HAJIRASOULIAN Mohammadre. Male Coach C IRI IR Iran Islamic Republic of Iran Artistic Gymnastics null 1965-06-27 1540258 true DAVIS DIAZ David Male Coach C MEX Mexico Mexico Taekwondo null 1977-10-07 1540259 true MENDOZA MORA Abel Male Coach C MEX Mexico Mexico Taekwondo null 1988-02-26 1540260 true VICTORIA ESPINOSA de los Alfonso Male Coach C MEX Mexico Mexico Taekwondo null 1985-02-01 1540522 true MILANO Guillermo Male Head Coach C ARG Argentina Argentina Handball Men 1973-02-08 1540638 true GOMEZ CORA Santiago Male Head Coach C ARG Argentina Argentina Rugby Sevens Men 1978-07-25 1540639 true GRAVANO Leonardo Male Assistant Coach C ARG Argentina Argentina Rugby Sevens Men 1973-08-30 1540840 true FILIORIANU Ana Luiza Female Coach C ROU Romania Romania Rhythmic Gymnastics null 1999-07-10 1542341 true SMAILI Badr Male Coach C MAR Morocco Morocco Taekwondo null 1993-05-07 1542904 true OCEGUERA ORNELAS Pavel Male Coach C MEX Mexico Mexico Artistic Gymnastics null 1971-09-10 1542908 true VALENZUELA GOMEZ Maria Female Coach C MEX Mexico Mexico Artistic Gymnastics null 1976-07-23 1542913 true MEZA PADILLA Jose Male Coach C MEX Mexico Mexico Artistic Gymnastics null 1977-01-25 1542973 true AGUILAR ROJAS Blajaith Female Coach C MEX Mexico Mexico Rhythmic Gymnastics null 1991-09-30 1542976 true FURALEV Vladislav Male Coach C MEX Mexico Mexico Rhythmic Gymnastics null 1970-01-04 1543567 true UPTON Patrick Anthony Howard Male Coach C IND India India Hockey null 1968-11-05 1543570 true SCHOPMAN Johanna Dorothea Maria Female Coach C IND India India Hockey null 1977-04-26 1543575 true HALKETT Rhett Kennedy Male Assistant Coach C IND India India Hockey null 1986-05-02 1543576 true FULTON Craig Arthur Male Head Coach C IND India India Hockey null 1974-11-06 1543577 true FARRY Anthony James Male Coach C IND India India Hockey null 1973-07-13 1544157 true THORPE Karen Female Coach C GBR Great Britain Great Britain Artistic Swimming Duet 1973-04-21 1544158 true TOMOMATSU Yumiko Female Coach C GBR Great Britain Great Britain Artistic Swimming Duet 1972-07-21 1544489 true CURRAN Orlaith Female Assistant Coach C IRL Ireland Ireland Rugby Sevens Women 1990-08-08 1545106 true NASKAR Arup Male Coach C IND India India Hockey null 1983-05-05 1545139 true CHINNASAMY Ashok Kumar Male Coach C IND India India Hockey null 1991-04-24 1545947 true BUSNARI Alberto Male Coach C ITA Italy Italy Artistic Gymnastics null 1978-10-04 1545949 true COCCIARO Giuseppe Male Coach C ITA Italy Italy Artistic Gymnastics null 1959-08-05 1545950 true FORTUNA Marco Male Coach C ITA Italy Italy Artistic Gymnastics null 1961-06-06 1545955 true BERGAMELLI Monica Roberta Female Coach C ITA Italy Italy Artistic Gymna

In [0]:
coaches = _sqldf
coaches.show()

+-------+-------+--------------------+------+---------------+--------+------------+---------+--------------------+-------------------+------+----------+
|   code|current|                name|gender|       function|category|country_code|  country|        country_long|        disciplines|events|birth_date|
+-------+-------+--------------------+------+---------------+--------+------------+---------+--------------------+-------------------+------+----------+
|1533246|   true|      PEDRERO Ofelia|Female|          Coach|       C|         MEX|   Mexico|              Mexico|  Artistic Swimming|  Team|1988-03-28|
|1535775|   true|    RADHI SHENAISHIL|  Male|     Head Coach|       C|         IRQ|     Iraq|                Iraq|           Football|   Men|1965-07-01|
|1536055|   true| AFLAKIKHAMSEH Majid|  Male|          Coach|       C|         IRI|  IR Iran|Islamic Republic ...|          Taekwondo|  NULL|1973-08-26|
|1536059|   true|     YOUSEFY Mehrdad|  Male|          Coach|       C|         IRI

## Data Export

The transformed data is saved to Azure Data Lake Storage as CSV files. Each DataFrame (athletes, medals, coaches, and teams) is repartitioned into a single file and written with headers, overwriting any existing files in the destination directory.


In [0]:
athletes.repartition(1).write.mode("overwrite").option("header",'true').csv("/mnt/parisolymics/transformed-data/athletes")
medals.repartition(1).write.mode("overwrite").option("header",'true').csv("/mnt/parisolymics/transformed-data/medals")
coaches.repartition(1).write.mode("overwrite").option("header",'true').csv("/mnt/parisolymics/transformed-data/coaches")
teams.repartition(1).write.mode("overwrite").option("header",'true').csv("/mnt/parisolymics/transformed-data/teams")

